<a href="https://colab.research.google.com/github/ratmcu/wiki_ner/blob/master/wiki_conll_dataset.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [74]:
!pip install wget
import os
import wget
import logging
logger = logging.getLogger()
logger.setLevel(logging.INFO)
try:
    import colabimport
except:
    colabimporturl = 'https://github.com/ratmcu/colaboratory_import/raw/master/colabimport.py'
    filename = colabimporturl.split("/")[-1].split("?")[0]
    if os.path.isfile(filename):
        os.remove(filename)
    wget.download(colabimporturl)
    import colabimport
    
colabimport.get_notebook('https://github.com/ratmcu/wiki_ner/blob/master/conll_tagged_ne.ipynb?raw=true')
from conll_tagged_ne import WikiConLLTagger
class HashableTupleAnnotations(tuple):
    def __hash__(self):
        return hash(tuple(sorted([self[0:1],self[1:2]])))
class hashabledict(dict):
    def __hash__(self):
        return hash(tuple(sorted(self.items())))
!pip install spacy
!python -m spacy download en_core_web_sm
import spacy
nlp = spacy.load("en_core_web_sm")
import re
!pip install pyahocorasick
!pip install fuzzyset
from ahocorasick import Automaton
import fuzzyset
from operator import itemgetter, attrgetter
import pandas as pd
import pickle
import urllib
from bs4 import BeautifulSoup
import numpy as np
import json

✔ Download and installation successful
You can now load the model via spacy.load('en_core_web_sm')


In [0]:
#experiment_code
# tagger = WikiConLLTagger('https://en.wikipedia.org/wiki/Barack_Obama')
tagger = WikiConLLTagger('https://en.wikipedia.org/wiki/Donald_Trump')
print(tagger.get_metadata())
with open('meta_data.pkl', 'wb') as f:
    pickle.dump(tagger.get_metadata(), f)

In [0]:
#experiment_code
df = pd.DataFrame(data = tagger.place_tags())
df.to_csv(r'conll_annot.csv', index = None, header=True)

In [0]:
wget.download('https://github.com/ratmcu/wiki_ner/blob/master/president_list.pkl?raw=true')
category = 'politicians'

## pipeline this to accomodate other categories

with open('president_list.pkl', 'rb') as f:
    prsdnt_list = pickle.load(f)
print(prsdnt_list)
for cntry in prsdnt_list:
    for prsdnt in cntry['presidents']:
        if cntry['country'] and prsdnt['name']:
            path = 'dataset' + '/' + category + '/' + cntry['country'] + '/' +  prsdnt['name']
        else:
            continue
        if not os.path.exists(path):
            os.makedirs(path)
        else:
            continue
        try:
            tagger = WikiConLLTagger(prsdnt['url'])
            df = pd.DataFrame(data = tagger.place_tags())
            df.to_csv(r'{0}/conll_tagged.csv'.format(path), index = None, header=True)
        except:
            print("failed to annotate the page!")
            print(prsdnt['url'])
            
import tarfile
tar =  tarfile.open('dataset.tar.gz', mode='w:gz')
tar.add('dataset')
tar.close()    


[{'country': 'United Nations System', 'url': 'https://en.wikipedia.org/wiki/United_Nations_System', 'presidents': []}, {'country': 'Member states of the United Nations', 'url': 'https://en.wikipedia.org/wiki/Member_states_of_the_United_Nations', 'presidents': []}, {'country': 'Afghanistan', 'url': 'https://en.wikipedia.org/wiki/Afghanistan', 'presidents': [{'name': 'Ashraf Ghani', 'url': 'https://en.wikipedia.org/wiki/Ashraf_Ghani'}, {'name': 'Hamid Karzai', 'url': 'https://en.wikipedia.org/wiki/Hamid_Karzai'}, {'name': 'Sibghatullah Mojaddedi', 'url': 'https://en.wikipedia.org/wiki/Sibghatullah_Mojaddedi'}, {'name': 'Babrak Karmal', 'url': 'https://en.wikipedia.org/wiki/Babrak_Karmal'}, {'name': 'Hafizullah Amin', 'url': 'https://en.wikipedia.org/wiki/Hafizullah_Amin'}, {'name': 'Burhanuddin Rabani', 'url': 'https://en.wikipedia.org/wiki/Burhanuddin_Rabani'}, {'name': 'Abdul Rahim Hatif', 'url': 'https://en.wikipedia.org/wiki/Abdul_Rahim_Hatif'}, {'name': 'Haji Mohammad Chamkani', 'ur

In [0]:
import tarfile
tar =  tarfile.open('metadata.tar.gz', mode='w:gz')
tar.add('metadata')
tar.close()

In [3]:
quote_page = 'https://en.wikipedia.org/w/index.php?title=Category:Possibly_living_people'
# quote_page = 'https://en.wikipedia.org/wiki/Category:Living_people'
# page = urllib.request.urlopen(quote_page)
# soup = BeautifulSoup(page, 'html.parser')

def stack_category_links(url, links):
    page = urllib.request.urlopen(url)
    soup = BeautifulSoup(page, 'html.parser')
    content_big = soup.find('div', attrs={'class': 'mw-content-ltr'}) # or infobox biography vcard
    link_list = content_big.find('div', attrs={'class': 'mw-category'}) # or infobox biography vcard
    links.extend(link_list.find_all('a'))
    next_page = content_big.next_sibling.next_sibling.a.get('href')
    try:
        stack_category_links(next_page, links)
    except:
        return links
    return links

links = []
stack_links(quote_page, links)

[<a href="/wiki/Judge_Edward_Aaron" title="Judge Edward Aaron">Judge Edward Aaron</a>,
 <a href="/wiki/Mohamed_Jamshid_Abadi" title="Mohamed Jamshid Abadi">Mohamed Jamshid Abadi</a>,
 <a href="/wiki/Abbas_Sami%27i" title="Abbas Sami'i">Abbas Sami'i</a>,
 <a href="/wiki/Abdul_Rashid_Abbasi" title="Abdul Rashid Abbasi">Abdul Rashid Abbasi</a>,
 <a href="/wiki/Ibrahim_Abdel_Hamid" title="Ibrahim Abdel Hamid">Ibrahim Abdel Hamid</a>,
 <a href="/wiki/Mohamed_Abdel-El" title="Mohamed Abdel-El">Mohamed Abdel-El</a>,
 <a href="/wiki/Ibrahim_Abdrabbou" title="Ibrahim Abdrabbou">Ibrahim Abdrabbou</a>,
 <a href="/wiki/Qazi_Abdul_Waheed" title="Qazi Abdul Waheed">Qazi Abdul Waheed</a>,
 <a href="/wiki/Abdulganiyu_Abdulrasaq" title="Abdulganiyu Abdulrasaq">Abdulganiyu Abdulrasaq</a>,
 <a href="/wiki/Ben_Sa%C3%AFd_Abdallah" title="Ben Saïd Abdallah">Ben Saïd Abdallah</a>,
 <a href="/wiki/Hiroshi_Abe_(war_criminal)" title="Hiroshi Abe (war criminal)">Hiroshi Abe (war criminal)</a>,
 <a href="/wiki/Os

In [25]:
print(len(links))
print(links[0])
print(links[0].get('href'))
# [ str(link.a.get('href')) for link in links ]

188200
<a href="/wiki/Judge_Edward_Aaron" title="Judge Edward Aaron">Judge Edward Aaron</a>
/wiki/Judge_Edward_Aaron


In [0]:
import sys
sys.getsizeof(links)
import pickle
import json
js = json.dumps([ str(link.get('href')) for link in links ] )
with open('Living_people.pkl', 'wb') as f:
    pickle.dump(js, f)

## **Mining for Categories**

In [34]:
with open('Living_people.pkl', 'rb') as f:
    js = pickle.load(f)
js

'["/wiki/Judge_Edward_Aaron", "/wiki/Mohamed_Jamshid_Abadi", "/wiki/Abbas_Sami%27i", "/wiki/Abdul_Rashid_Abbasi", "/wiki/Ibrahim_Abdel_Hamid", "/wiki/Mohamed_Abdel-El", "/wiki/Ibrahim_Abdrabbou", "/wiki/Qazi_Abdul_Waheed", "/wiki/Abdulganiyu_Abdulrasaq", "/wiki/Ben_Sa%C3%AFd_Abdallah", "/wiki/Hiroshi_Abe_(war_criminal)", "/wiki/Osamu_Abe_(rower)", "/wiki/Maria_do_Carmo_Abecassis", "/wiki/Youssef_Abou_Ouf", "/wiki/Ahmed_Abou-Shadi", "/wiki/Ahmad_Shah_Abouwi", "/wiki/Andrei_Abraham", "/wiki/Faghme_Abrahams", "/wiki/Elisabeta_Abrudeanu", "/wiki/Anton%C3%ADn_Absolon", "/wiki/Milada_Absolonov%C3%A1", "/wiki/Rauf_Abu_Al-Seoud", "/wiki/Aziz_al-Abub", "/wiki/Roqia_Abubakr", "/wiki/A._R._A._M._Abubucker", "/wiki/Perla_Ach%C3%A1val", "/wiki/Juli%C3%A1n_Acosta", "/wiki/Geormbeeyi_Adali-Mortty", "/wiki/Dimitrios_Adamou", "/wiki/Don_Adams_(boxer)", "/wiki/Jimmy_Adamson_(Scottish_footballer)", "/wiki/Tommy_Adamson", "/wiki/Aden_Isaq_Ahmed", "/wiki/Antonio_Adipe", "/wiki/Gharib_Afifi", "/wiki/Faiz_Af

In [0]:
def add_wiki_prefix(func):
    def wrapper(url):
        url = 'https://en.wikipedia.org' + url
        return func(url)
    return wrapper

@add_wiki_prefix
def get_category_list(url):
    page = urllib.request.urlopen(url)
    soup = BeautifulSoup(page, 'html.parser')
    catlink_box = soup.find('div', attrs={'class': 'mw-normal-catlinks'}) # or infobox biography vcard
    return [ li.text for li in catlink_box.find_all('li')]

In [76]:
ss = set(category for category in get_category_list('/wiki/Category:Dead_people'))
_ = [ss.add(category) for category in get_category_list('/wiki/Category:Living_people')]
print(ss)
ll = list(ss)
df = pd.DataFrame()
df1 =  pd.DataFrame(np.ones((1,len(ll)), dtype=np.int64), columns=ll)
df = df.append(df1, ignore_index=False, sort=False)
# df1[ll[0]] += 1
ll2 = ['Life', 'People by status', 'Criminals']
df2 = pd.DataFrame(np.ones((1,len(ll2)), dtype=np.int64), columns=ll2)
df = df.append(df2, ignore_index=False, sort=False)
print(df)

{'Survivors', 'Death', 'Life', 'People by status'}
   Survivors  Death  Life  People by status  Criminals
0        1.0    1.0     1                 1        NaN
0        NaN    NaN     1                 1        1.0


In [88]:
import ast
with open('Living_people.pkl', 'rb') as f:
    js = pickle.load(f)
# js = json.load(js)    
links_js = ast.literal_eval(js)
print(links_js[0])
category_df =  pd.DataFrame()
for i, link in enumerate(links_js):
    print(i, link)
    cats = [category for category in get_category_list(str(link))]
    df_cats =  pd.DataFrame(np.ones((1,len(cats)), dtype=np.int64), columns=cats)
    category_df = category_df.append(df_cats)
    if i == 100:
        break
    
category_df

/wiki/Judge_Edward_Aaron
0 /wiki/Judge_Edward_Aaron
1 /wiki/Mohamed_Jamshid_Abadi


/usr/local/lib/python3.6/dist-packages/pandas/core/frame.py:6692: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.

  sort=sort)


2 /wiki/Abbas_Sami%27i
3 /wiki/Abdul_Rashid_Abbasi
4 /wiki/Ibrahim_Abdel_Hamid
5 /wiki/Mohamed_Abdel-El
6 /wiki/Ibrahim_Abdrabbou
7 /wiki/Qazi_Abdul_Waheed
8 /wiki/Abdulganiyu_Abdulrasaq
9 /wiki/Ben_Sa%C3%AFd_Abdallah
10 /wiki/Hiroshi_Abe_(war_criminal)
11 /wiki/Osamu_Abe_(rower)
12 /wiki/Maria_do_Carmo_Abecassis
13 /wiki/Youssef_Abou_Ouf
14 /wiki/Ahmed_Abou-Shadi
15 /wiki/Ahmad_Shah_Abouwi
16 /wiki/Andrei_Abraham
17 /wiki/Faghme_Abrahams
18 /wiki/Elisabeta_Abrudeanu
19 /wiki/Anton%C3%ADn_Absolon
20 /wiki/Milada_Absolonov%C3%A1
21 /wiki/Rauf_Abu_Al-Seoud
22 /wiki/Aziz_al-Abub
23 /wiki/Roqia_Abubakr
24 /wiki/A._R._A._M._Abubucker
25 /wiki/Perla_Ach%C3%A1val
26 /wiki/Juli%C3%A1n_Acosta
27 /wiki/Geormbeeyi_Adali-Mortty
28 /wiki/Dimitrios_Adamou
29 /wiki/Don_Adams_(boxer)
30 /wiki/Jimmy_Adamson_(Scottish_footballer)
31 /wiki/Tommy_Adamson
32 /wiki/Aden_Isaq_Ahmed
33 /wiki/Antonio_Adipe
34 /wiki/Gharib_Afifi
35 /wiki/Faiz_Aftab
36 /wiki/Dante_Agostini_(canoer)
37 /wiki/Manuel_Ag%C3%BCero
38

1909 births  ...  Wrestlers at the 1952 Summer Olympics
0           NaN  ...                                    NaN
0           NaN  ...                                    NaN
0           NaN  ...                                    NaN
0           NaN  ...                                    NaN
0           NaN  ...                                    NaN
0           NaN  ...                                    NaN
0           NaN  ...                                    NaN
0           NaN  ...                                    NaN
0           NaN  ...                                    NaN
0           NaN  ...                                    NaN
0           NaN  ...                                    NaN
0           NaN  ...                                    NaN
0           NaN  ...                                    NaN
0           NaN  ...                                    NaN
0           1.0  ...                                    NaN
0           NaN  ...                                    NaN
0           NaN  ...                                    NaN
0           NaN  ...                                    NaN
0           NaN  ...                                    NaN
0           NaN  ...                                    NaN
0           NaN  ...                                    NaN
0           NaN  ...                                    NaN
0           NaN  ...                                    NaN
0           NaN  ...                                    NaN
0           NaN  ...                                    NaN
0           NaN  ...                                    NaN
0           NaN  ...                                    NaN
0           NaN  ...                                    NaN
0           NaN  ...                                    NaN
0           NaN  ...                                    NaN
..          ...  ...                                    ...
0           NaN  ...                                    NaN
0           NaN  ...                                    NaN
0           NaN  ...                                    NaN
0           NaN  ...                                    NaN
0           NaN  ...                                    NaN
0           NaN  ...                                    NaN
0           NaN  ...                                    NaN
0           NaN  ...                                    NaN
0           NaN  ...                                    NaN
0           NaN  ...                                    NaN
0           NaN  ...                                    NaN
0           NaN  ...                                    NaN
0           NaN  ...                                    NaN
0           NaN  ...                                    NaN
0           NaN  ...                                    NaN
0           NaN  ...                                    NaN
0           NaN  ...                                    NaN
0           NaN  ...                                    NaN
0           NaN  ...                                    NaN
0           NaN  ...                                    NaN
0           NaN  ...                                    NaN
0           NaN  ...                                    NaN
0           NaN  ...                                    NaN
0           NaN  ...                                    NaN
0           NaN  ...                                    NaN
0           NaN  ...                                    NaN
0           NaN  ...                                    NaN
0           NaN  ...                                    NaN
0           NaN  ...                                    NaN
0           NaN  ...                                    NaN

[101 rows x 433 columns]

In [90]:
import sys
print(len(category_df.columns), sys.getsizeof(category_df))

433 350696
